# EPS109 Final Project
## By Joshua Delrosario

In [2]:
import numpy as np
import matplotlib.pyplot as plt
%matplotlib qt

In [3]:
def display(A):
    %matplotlib qt
    
    plt.rcParams['figure.figsize'] = [6, 6/maxX*maxY]
    plt.imshow(A); 
    plt.axis('off'); 
    plt.show()
    plt.draw()

In [4]:
def circleCheck(origin_x, origin_y, check_x, check_y, radius):
    dx = origin_x - check_x
    dy = origin_y - check_y;
    distance_squared = dx*dx + dy*dy;
    return distance_squared <= radius*radius;

In [5]:
from matplotlib.animation import FFMpegWriter

In [6]:
from matplotlib import cm
from matplotlib.colors import ListedColormap

b = cm.get_cmap('winter', 10)
colors = b(np.linspace(0,1,100))
black = np.array([0, 0, 0, 1])
white = np.array([1, 1, 1, 1])
orange = np.array([255/255, 127/255, 0, 1])
green = np.array([0, 100/255, 0, 1])
colors[10:20] = black
colors[:10] = white
colors[90:100] = orange
colors[80:90] = green
newcmp = ListedColormap(colors)

cm.register_cmap("breakout", newcmp)

In [7]:
class Ball:
    def __init__(self, startX, startY, startVelX=0, startVelY=0, ballVal=4):
        self.x = startX
        self.y = startY
        self.v_x = startVelX
        self.v_y = startVelY
        self.value = ballVal
        self.idx = -1
        self.type = "ball"
    
    def setIdx(self, new_idx):
        self.idx = new_idx
        
    def collision(self, game_state, offending_coord):
        if self.idx != game_state.object_matrix[offending_coord[1], offending_coord[0]]:
            print("ball collision detected!")
            print("My idx:", self.idx)
            print("Your idx:", game_state.object_matrix[offending_coord[1], offending_coord[0]])

    def tick(self):
        return None

In [56]:
class Block:
    def __init__(self, startX, startY, initial_height, initial_width, blockValue=3):
        self.xCorner = startX
        self.yCorner = startY
        self.height = initial_height
        self.width = initial_width
        self.value = blockValue
        self.type = "block"
        
    def collision(self, game_state, offending_coord):
        placeBlock(Block(self.xCorner, self.yCorner, self.height, self.width, 0), game_state.board, game_state.object_matrix, 0)
        
        
def placeBlock(block, board, object_matrix, object_id):
    for y in range(block.yCorner, block.yCorner + block.height - 1):
        for x in range(block.xCorner, block.xCorner + block.width - 1):
            board[y, x] = block.value
            object_matrix[y, x] = object_id

class GameState:
    def __init__(self, board, object_matrix, object_list, ball_list):
        self.board = board
        self.object_matrix = object_matrix
        self.object_list = object_list
        self.ball_list = ball_list

    def spawn_ball(self, ball):
        # print("Trying to spawn a ball!")
        self.ball_list.append(ball)
        self.board[ball.y, ball.x] = ball.value
        ball.setIdx(len(self.object_list)-1)
        self.object_matrix[ball.y, ball.x] = ball.idx
        self.object_list.append(ball)

In [29]:
def runSim(name, T, ball_list, max_iterations, object_matrix, object_list):
    metadata = dict(title='EPS109 Final Project', artist='Joshua Delrosario')
    writer = FFMpegWriter(fps=20, metadata=metadata)
    fig = plt.figure()
    plt.rcParams['animation.ffmpeg_path']=r'C:\Program Files\ffmpeg\bin\ffmpeg.exe'
    filename = name + ".mp4"
    game_state = GameState(T, object_matrix, object_list, ball_list)
    
    # Initialize Writer
    with writer.saving(fig, filename, dpi=400):
        # BEGIN SIMULATION LOOP
        print("Beginning sim with " + str(max_iterations) + " iterations.")
        for i in range(0, max_iterations):
            for b in ball_list:
                T[b.y, b.x] = 0
                object_matrix[b.y, b.x] = 0
                
                new_x = b.x
                new_y = b.y
                
                to_travel_x = abs(b.v_x)
                to_travel_y = abs(b.v_y)
                for _ in range(0, max(abs(b.v_x), abs(b.v_y))):
                    old_x = new_x
                    old_y = new_y
                    if to_travel_x > 0:
                        old_x = new_x
                        new_x = new_x + (b.v_x // abs(b.v_x))
                        to_travel_x -= 1
                        if T[new_y, new_x] > 0:
                            target_index = int(object_matrix[new_y, new_x])
                            if target_index > 0:
                                b.collision(game_state, [new_x, new_y])
                                object_list[target_index].collision(game_state, [new_x, new_y])
                            b.v_x = b.v_x * -1
                            new_x = old_x
                            break
                    if to_travel_y > 0:
                        old_y = new_y
                        new_y = new_y + (b.v_y // abs(b.v_y))
                        to_travel_y -= 1
                        if T[new_y, new_x] > 0:
                            target_index = int(object_matrix[new_y, new_x])
                            if target_index > 0:
                                b.collision(game_state, [new_x, new_y])
                                object_list[target_index].collision(game_state, [new_x, new_y])
                            b.v_y = b.v_y * -1
                            new_y = old_y
                            break
                    #print("Attempting to go to ("+str(new_x)+", "+str(new_y)+"). The value at this coord is " +str(T[new_y, new_x]))
                b.x = new_x
                b.y = new_y
                T[b.y, b.x] = b.value
                object_matrix[b.y, b.x] = b.idx
                b.tick()
            fig.clear()
            plt.imshow(T, cmap='breakout')
            plt.axis('off')
            plt.draw()
            plt.pause(0.01)
            writer.grab_frame()
            if i % (max_iterations // 10) == 0:
                print("Iteration" + str(i) + "...")
    fig.clear()
    print("Sim Complete")
        
        
def gameWrapper(name, ball_list, block_list, max_iterations, maxX=125, maxY=125):
    T = np.zeros((maxX, maxY))
    object_matrix = np.zeros((maxX, maxY))
    object_list = [None]
    
    for i in range(0, maxX):
        for j in range(0, maxY):
            if j == 0 or j == maxY-1 or i == 0 or i==maxX-1:
                T[j, i] = 1
    for ball in ball_list:
        object_list.append(ball)
        T[ball.y, ball.x] = ball.value
        ball.setIdx(len(object_list)-1)
        object_matrix[ball.y, ball.x] = ball.idx
        
    for block in block_list:
        object_list.append(block)
        placeBlock(block, T, object_matrix, len(object_list)-1)

    runSim(name, T, ball_list, max_iterations, object_matrix, object_list)

In [30]:
maxX = 125
maxY = 125
iters = 60
name = "dev"

#ball1 = Ball(20, 10, 2, -3, 8)
#ball2 = Ball(10, maxY//4, -3, -2, 9)

ball1 = Ball(5, 10, 1, 0, 9)
ball2 = Ball(10, 10, -2, 0, 8)
balls = [ball1, ball2]


blocks = []

#gameWrapper(name, balls, blocks, iters, 20, 20)

def breakoutSim():
    name = "breakout_dev"
    iters = 500
    maxX = 125
    maxY = 125
    b_wid = 10
    b_hei = 5
    ball1 = Ball(20, 10, 2, -3, 8)
    ball2 = Ball(10, maxY//4, -3, -2, 9)
    balls = [ball1, ball2]
    for j in range(0, 4):
        for i in range(0, 11):
            new_block = Block(8 + i * b_wid, 25 + j * b_hei, 5, 10, 4)
            blocks.append(new_block)
    gameWrapper(name, balls, blocks, iters, maxX, maxY)

In [53]:
MASTER_RNG_SEED = 12345
rng = np.random.default_rng(MASTER_RNG_SEED)


def findFreeSpace(my_x, my_y, matrix):
    free_spaces = []
    for j in range(0, 3):
        for i in range(0, 3):
            new_x = my_x - 1 + i
            new_y = my_y - 1 + j
            if new_x >= 0 and new_y >= 0 and new_x < matrix.shape[1] and new_y < matrix.shape[0]:
                if int(matrix[new_y, new_x]) == 0:
                    free_spaces.append([new_y, new_x])
    if len(free_spaces) == 0:
        return None
    return free_spaces[rng.integers(len(free_spaces))]



# The splitter has a chance to split itself on collision
class Splitter:
    
    def __init__(self, startX, startY, startVelX, startVelY, ballVal=4, init_split_chance=0.0, initial_tick_wait=5, free_split=False):
        self.x = startX
        self.y = startY
        self.v_x = startVelX
        self.v_y = startVelY
        self.value = ballVal
        self.split_chance = init_split_chance
        self.idx = -1
        self.cd = initial_tick_wait
        self.free_split = free_split

    def setIdx(self, new_idx):
        self.idx = new_idx

    def collision(self, game_state, offending_coord):
        #if self.idx != game_state.object_matrix[offending_coord[1], offending_coord[0]]:
        roll = rng.random()
        if self.free_split or (roll < self.split_chance and self.cd < 1):
            self.free_split = False
            new_x = rng.integers(max(1, abs(self.v_x)) * 2) - self.v_x
            new_y = rng.integers(max(1, abs(self.v_y)) * 2) - self.v_y
            while new_x == 0 and new_y == 0:
                new_x = rng.integers(max(1, abs(self.v_x)) * 2) - self.v_x
                new_y = rng.integers(max(1, abs(self.v_y)) * 2) - self.v_y
            free_spot = findFreeSpace(self.x, self.y, game_state.board)
            if free_spot is not None:
                self.cd = 4
                clone = Splitter(free_spot[1], free_spot[0], new_x, new_y, self.value, self.split_chance)
                game_state.spawn_ball(clone)

    def tick(self):
        self.cd -= 1

In [52]:

def splitterSim():
    maxX = 50
    maxY = 50
    iters = 200
    name = "dev_splitter"

    #ball1 = Ball(20, 10, 2, -3, 8)
    #ball2 = Ball(10, maxY//4, -3, -2, 9)

    ball1 = Splitter(5, 5, 2, 2, 9, .5, 0)
    ball2 = Splitter(40, 40, -2, -2, 8, .5, 0)
    balls = [ball1, ball2]


    blocks = []

    gameWrapper(name, balls, blocks, iters, maxX, maxY)
splitterSim()

Beginning sim with 200 iterations.
Iteration0...
Trying to spawn a ball!
Iteration20...
Iteration40...
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Iteration60...
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Iteration80...
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Iteration100...
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to s

Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn 

Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn 

Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn 

Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn 

...

Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn 

Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn 

Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn 

Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn a ball!
Trying to spawn 

KeyboardInterrupt: 

In [60]:
def breakoutWithSplitterSim():
    name = "breakout_with_splitter"
    iters = 300
    maxX = 125
    maxY = 125
    b_wid = 10
    b_hei = 5
    ball1 = Splitter(maxX // 2, maxY - 20, 2, -2, 8, .5, 0, free_split=True)
    balls = [ball1]
    for j in range(0, 4):
        for i in range(0, 11):
            new_block = Block(8 + i * b_wid, 25 + j * b_hei, 5, 10, 4)
            blocks.append(new_block)
    gameWrapper(name, balls, blocks, iters, maxX, maxY)
breakoutWithSplitterSim()

Beginning sim with 300 iterations.
Iteration0...
Iteration30...
Iteration60...
Iteration90...
Iteration120...
Iteration150...
Iteration180...
Iteration210...
Iteration240...
Iteration270...


KeyboardInterrupt: 